In [1]:
import numpy as np

import matplotlib.pyplot as plt

from multiprocess import Pool
from functools import partial
import numpy as np

import games

import cpb
# import cpb_uniform
import cpb_gaussian

import random_algo

import plotly.graph_objects as go
from sklearn.preprocessing import PolynomialFeatures

import synthetic_data
import cpb_side
import cpb_side_gaussian


import gzip
import pickle as pkl

import linucb



def evaluate_parallel(nbCores, n_folds, horizon, alg, game, type, context_type):
    print("nbCores:", nbCores, "nbFolds:", n_folds, "Horizon:", horizon)
    pool = Pool(processes = nbCores) 
    task = Evaluation(horizon, type)

    np.random.seed(1)
    distributions = []
    context_generators = []

    for jobid in range(n_folds):
        
        p = np.random.uniform(0, 0.2) if type == 'easy' else np.random.uniform(0.4,0.5)
        distributions.append( [p, 1-p] )

        contexts = synthetic_data.QuinticContexts( 2, 0.01)
        context_generators.append( contexts )

        # d = 2
        # margin =0.01
        # contexts = synthetic_data.LinearContexts( np.array([0.5,0.5]), 0, d, margin) #synthetic_data.ToyContexts( )

    return np.asarray(  pool.map( partial( task.eval_policy_once, alg, game ), zip(distributions , context_generators ,range(n_folds)) ) ) 

class Evaluation:

    def __init__(self, horizon,type ):
        self.type = type
        self.horizon = horizon
        # self.outcome_distribution = outcome_distribution

    def get_outcomes(self, game, job_id):
        # self.means = runif_in_simplex( self.game.n_outcomes )
        outcomes = np.random.choice( game.n_outcomes , p= list( game.outcome_dist.values() ), size= self.horizon) 
        return outcomes

    def get_feedback(self, game, action, outcome):
        return game.FeedbackMatrix[ action ][ outcome ]

    def get_bandit_feedback(self, game, action, outcome):
        return game.banditFeedbackMatrix[ action ][ outcome ]

    def eval_policy_once(self, alg, game, job):

        distribution, context_generator, jobid = job

        np.random.seed(jobid)

        # outcome_distribution =  {'spam':0.5,'ham':0.5}
        outcome_distribution =  {'spam':distribution[0],'ham':distribution[1]}

        game.set_outcome_distribution( outcome_distribution, jobid )
        #print('optimal action', game.i_star)

        # action_counter = np.zeros( (game.n_actions, self.horizon) )

        # generate outcomes obliviously
        outcomes = self.get_outcomes(game, jobid)
        contexts = [ context_generator.get_context(outcome) for outcome in outcomes ]
        # context_generator.generate_unique_context()
        # contexts = [ context_generator.get_same_context(outcome) for outcome in outcomes ]

        contexts = np.array(contexts).squeeze()
        contexts = PolynomialFeatures(6).fit_transform( contexts)
        contexts = contexts.tolist()
        dim = len(contexts[0])
        contexts = [ np.array(elmt).reshape( (dim,1) ) for elmt in contexts]

        cumRegret =  np.zeros(self.horizon, dtype =float)

        alg.reset()

        for t in range(self.horizon):

            # if t % 1000 == 0 :
            #     print(t)

            # Environment chooses one outcome and one context associated to this outcome
            outcome = outcomes[t]
            context = contexts[t]

            # print(context.T.shape)
            # policy chooses one action
            # print('t', t,  'outcome', outcome, 'context', context)
            action = alg.get_action(t, context)
            # print('t', t, 'action', action, 'outcome', outcome, 'context', context)
            
            feedback =  self.get_feedback( game, action, outcome )
            bandit_feedback =  self.get_bandit_feedback( game, action, outcome )

            alg.update(action, feedback, outcome, t, context )
            
            # print('nu', alg.nu / alg.n )
            regret = game.LossMatrix[action, outcome] - np.min( game.LossMatrix[...,outcome] )
            # print( 'regret:' , regret )
            cumRegret[t] =  regret
            # print()
            # print()
        # regret = np.array( [ game.delta(i) for i in range(game.n_actions) ]).T @ action_counter
        #context_regret = np.cumsum( 
        # cumRegret )

        print('job done')

        return  np.cumsum( cumRegret ) #regret

In [ ]:
import PGIDSratio

n_cores = 8
n_folds = 15
horizon = 20000

game =  games.apple_tasting( False ) 

alg = PGIDSratio.PGIDSratio( game, horizon, 28 )
task = Evaluation(horizon, 'difficult')

result = evaluate_parallel(n_cores, n_folds, horizon, alg, game, 'difficult', 'quintic')

# n_cores = 8
# n_folds = 8
# horizon = 1000

# result = evaluate_parallel(n_cores, n_folds, horizon, alg, game, 'easy')
# regret =  np.mean(result, 0) 
# xcoords = np.arange(0,horizon,1).tolist()
# std =  np.std(result,0) 

# plt.plot( regret )

In [ ]:
import PM_DMED

n_cores = 1
n_folds = 1
horizon = 100

# np.seterr(all='raise')

# game = games.apple_tasting(False, outcome_distribution) 

outcome_distribution = [0.8,0.2]
job = (outcome_distribution, 1 )


game =  games.label_efficient(  ) 
game.set_outcome_distribution( {'spam':outcome_distribution[0],'ham':outcome_distribution[1]} )
print('optimal action', game.i_star)


# print('optimal action', game.i_star)
alg = cpb.CPB(  game, horizon,1.01) #TSPM.TSPM_alg(  game, horizon, 1)
task = Evaluation(horizon, 'easy')

result = task.eval_policy_once(alg,game, job)
#plt.plot(range(horizon), result)
# fig = go.Figure( )
# regret = np.array([ game.delta(i) for i in range(game.n_actions) ]).T @ np.mean(result,0) 
# xcoords = np.arange(0,horizon,1).tolist()

# fig.add_trace(go.Scatter(x=xcoords, y=regret, line=dict(color='blue'), mode='lines',  name='TPSM' )) # 


In [62]:
import os


def loadall_results(path, horizon, n_folds):
    result = np.zeros( (n_folds, horizon) )
    with gzip.open(  path ,'rb') as f:
        for i in range(n_folds):
            try:
                result[i] = pkl.load(f)
            except EOFError:
                break
    return result


def loadall_results2(path, n_folds):
    result = np.zeros( (n_folds, 20000) )
    with gzip.open(  path ,'rb') as f:
        for i in range(n_folds):
            try:
                result[i] = pkl.load(f)[:20000]
            except EOFError:
                break
    return result

n_folds = 96
horizon = 20000

game = games.apple_tasting(False)

algos = [ None ]

# colors = [  [160, 32, 240], [250,0,0], [0,0,0]  ] 

# task = 'difficult'
# name = 'LE'
# context_type = 'linear'
# labels_latex = [ 'PGIDS', 'RandCBP', 'CBPside'  ] 
# labels = [   'PGIDSratio', 'RandCBP', 'CBPside' ]

# colors = [  [250,0,0], [0,0,0]  ] 

# task = 'difficult'
# name = 'LE'
# context_type = 'linear'
# labels_latex = [ 'RandCBP', 'CBPside'  ] 
# labels = [   'RandCBP', 'CBPside' ]

fig = go.Figure(    )

for color, label, label_latex in zip( colors, labels, labels_latex):

    r,g,b = color

    direct = './contextual_results/{}'.format(name)
    if label == 'RandCBP':
        path = os.path.join(direct, 'benchmark_{}_{}_100000_96_RandCBPside005_1_5_07.pkl.gz'.format(task,context_type) )
        result = loadall_results2(path, 96)

    elif label == 'CBPside':
        path = os.path.join(direct, '{}_{}_100000_96_CBPside005.pkl.gz'.format(task,context_type) )
        result = loadall_results2(path, 96)

    else: 
        path = os.path.join(direct, '{}_{}_{}_{}_{}.pkl.gz'.format(task,context_type, horizon, 96, label) )
        result = loadall_results(path, horizon, n_folds)

    worst_case = np.argmax( result[:,-1] )
    regret =  np.mean(result,0) 
    xcoords = np.arange(0,horizon,1).tolist() 
    upper_regret = result[worst_case]

    fig.add_trace(go.Scatter(x=xcoords, y=regret, line=dict(color='rgb({},{},{})'.format(r,g,b)), mode='lines',  name=label_latex,legendgrouptitle_text='Algorithm',legendgroup='Algorithm' ,  showlegend=False )) # 

    fig.add_trace(   go.Scatter( x=xcoords+xcoords[::-1], y=upper_regret.tolist()+regret.tolist()[::-1],  fill='toself', fillcolor='rgba({},{},{},0.2)'.format(r,g,b), 
                         line=dict(color='rgba({},{},{},0)'.format(r,g,b)),   hoverinfo="skip",  showlegend=False )  )
    
fig.update_layout( autosize=False,
                   xaxis_title="Sequence",
                   yaxis_title="Regret",
                   margin=go.layout.Margin( l=0,   r=0,   b=0,    t=0, ), 
                   font=dict(size=15,) ) #legend= dict(yanchor="top",y=0.98,xanchor="left",x=0.05)

fig.update_yaxes(range=[0, 2.7] )
fig.update_yaxes( type="log" )
fig.show(legend=False)

fig.write_image("./{}_{}_{}.pdf".format(task, name, context_type)  ) 


In [2]:
# game_name = 'AT'
# task = 'difficult'
# context_type = 'quintic'
# horizon = 20000
# n_folds = 15
# import subprocess
# label ='PGIDSratio'

# with gzip.open( './contextual_results/{}/{}_{}_{}_15_{}.pkl.gz'.format(game_name, task, context_type, horizon, label) ,'wb') as g:

#     for jobid in [71,72,74,75,77,82,83,84,88,89,90,92,93,94,95]:

#         with gzip.open(  './contextual_results/{}/{}_{}_{}_96_{}_{}.pkl.gz'.format(game_name, task, context_type, horizon, label, jobid) ,'rb') as f:
#             r = pkl.load(f)

#         pkl.dump( r, g)